## Build Training set for doc types

In [47]:
import TWB
import glob

In [30]:
import pandas as pd
import nltk
from nltk.stem import PorterStemmer
#from nltk.stem import LancasterStemmer
nltk.download('stopwords')
from nltk.corpus import stopwords
from nltk.tokenize import RegexpTokenizer

tokenizer = RegexpTokenizer(r'\w+')
porter = PorterStemmer()

[nltk_data] Downloading package stopwords to
[nltk_data]     /Users/sparaschiakos/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!


In [31]:
english_document_data = pd.read_pickle('data/english_document_data.pkl')
stems = pd.read_pickle('data/stemmed_data.pkl')
freq_content = pd.read_pickle('data/freq_content.pkl')

In [32]:
# defining function to check buzz word 
def exist_(temp,j): 
    temp2=temp.lower()
    temp3=temp2.find(j)
    return temp3>0
    
dictionary2=['certificate','instruction','poster','protocol', 'presentation',
             'response','letter','report','map','manual','banner']

for j in dictionary2:
    jj=english_document_data.Filename.apply(lambda x: exist_(x,j))
    rr=pd.DataFrame(columns=[str(j)])
    rr[str(j)]=jj
    english_document_data=pd.concat([english_document_data,rr ], axis=1)

In [33]:
# keep only the english ones
stems_en = stems.iloc[english_document_data.index]
freq_content_en = freq_content.iloc[english_document_data.index]

In [34]:
# drop dublicates and create the corpus
stems_en_noDbl = stems_en.drop_duplicates(subset='Content')
len(stems_en_noDbl.index)

6728

In [39]:
# create corpus
corpus = ''
for text in stems_en_noDbl.Content:
    corpus = corpus + text
# tokenize corpus
corpus_tok = tokenizer.tokenize(corpus)

In [41]:
corpus_tok = list(set(corpus_tok))
print(len(corpus_tok))

117229


In [136]:
# drop digits
corpus_tok_noDgt = []
for word in corpus_tok:
    if not word.isdigit():
        corpus_tok_noDgt.append(word)
len(corpus_tok_noDgt)

107119

In [35]:
# keep df with true in labels
df = english_document_data.loc[
    (english_document_data['certificate']==True) |
    (english_document_data['instruction']==True) |
    (english_document_data['poster']==True) |
    (english_document_data['protocol']==True) |
    (english_document_data['presentation']==True) |
    (english_document_data['response']==True) |
    (english_document_data['letter']==True) |
    (english_document_data['report']==True) |
    (english_document_data['map']==True) |
    (english_document_data['manual']==True) |
    (english_document_data['banner']==True)]

In [40]:
labeled_docs = pd.DataFrame(index= df.index, columns=['document', 'label'])

In [38]:
for i in df.index:
    go = False
    for j in df.columns:
        if (df[j][i] == True & go == False):
            labeled_docs.document[i] = df.Filename[i]
            labeled_docs.label[i] = j
            go = True

In [123]:
texts =[]

In [124]:
texts = list(stems_en_noDbl.Content)

In [125]:
token_freq = [ TWB.common.freq(t.split(' ')) for t in texts ]

In [126]:
token_freq[0]

{'': 1, 'test': 87, 'thi': 86}

In [127]:
dictionary = list(set(' '.join(texts).split(' ')))
dict_idx = { w : i for (i,w) in enumerate(dictionary) }
dict_idx

{'': 0,
 'wetransf': 1,
 'f0qu8': 2,
 'ngundik': 3,
 'யங': 4,
 'rheumatologist': 5,
 'unthread': 6,
 'cwfn': 7,
 'silvio': 8,
 'criminalis': 9,
 'burger': 10,
 'podemo': 11,
 'gelogor': 12,
 '20hr': 13,
 '၃': 14,
 'نیشتەجێ': 15,
 'EZ': 16,
 '01815335049': 17,
 'ebook': 18,
 'comm': 19,
 'hreint': 20,
 '419415ef749ed52c2fd9a27fb7057cf8': 21,
 'oe': 22,
 'ronaldhagan': 23,
 '1283dkk': 24,
 'toolon': 25,
 'faciltii': 26,
 'f0s9a': 27,
 'askira': 28,
 'corporación': 29,
 '2182': 30,
 'ሊገቡ': 31,
 'hyp': 32,
 '50g': 33,
 'livelihood': 34,
 '3131': 35,
 'ohg': 36,
 'laker': 37,
 'electeur': 38,
 'goor': 39,
 'raekoja': 40,
 'argyl': 41,
 'urmila': 42,
 '5c5503f5cf64e053d6378e551a640a0a': 43,
 'perfum': 44,
 'mezhdunarodnoy': 45,
 'cim': 46,
 'jarðskjálftar': 47,
 '32vb': 48,
 'کەمپ': 49,
 '6tmrkcdz4d2': 50,
 'sternal': 51,
 '21494': 52,
 'firstborn': 53,
 'crossrail': 54,
 'kyle': 55,
 'hood': 56,
 'testabl': 57,
 'countrycod': 58,
 'kmedmhmi13b': 59,
 'sinnar': 60,
 'leonora': 61,
 'sabor': 

In [128]:
import numpy as np
M = np.zeros((len(texts),len(dictionary)))

In [129]:
for i, text in enumerate(texts):
    M[i,[dict_idx[w] for w in token_freq[i].keys()]] = [x/sum(token_freq[i].values()) for x in  list(token_freq[i].values())]
    print(list(token_freq[i].values()))
M

[86, 87, 1]
[96, 97, 1]
[6, 2, 1, 1, 2, 1, 1, 1, 1, 2, 4, 1, 4, 1, 1, 2, 3, 2, 1, 1, 2, 1, 1, 1, 1, 1, 2, 2, 1, 2, 1, 1, 2, 2, 1, 2, 2, 1, 1, 3, 3, 3, 1, 1, 2, 2, 1, 1, 1, 1, 1, 3, 3, 3, 2, 1, 2, 3, 1, 1, 1, 2, 1, 1, 1, 1, 1, 1, 2, 1, 1, 1, 1, 1, 2, 1, 1, 2, 1, 1, 2, 2, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 2, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 2, 1, 1, 1, 1, 1, 1, 1, 1, 1]
[10, 3, 8, 2, 5, 3, 3, 1, 2, 2, 7, 5, 1, 1, 1, 1, 3, 1, 1, 4, 4, 4, 1, 4, 4, 2, 4, 2, 4, 4, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 1, 2, 4, 1, 1, 2, 2, 1, 1, 1, 1, 1, 1, 1, 1]
[137, 266, 130, 22, 95, 8, 13, 45, 15, 1, 1, 2, 5, 1, 1, 2, 5, 5, 32, 2, 1, 1, 3, 34, 29, 1, 64, 81, 15, 84, 7, 41, 176, 216, 3, 31, 162, 73, 6, 252, 52, 183, 6, 9, 6, 15, 8, 81, 214, 8, 71, 55, 52, 36, 176, 2, 37, 3, 31, 17, 2, 5, 1, 23, 12, 10, 35, 6, 17, 293, 83, 8, 10, 93, 32, 1, 24, 214, 370, 62, 1, 2, 135, 51, 186, 24, 19, 32, 36, 301, 18, 55, 68, 196, 7, 7, 5, 108, 25, 148, 45, 132, 32, 9, 23, 49, 74, 68, 3, 127, 104

[8, 4, 18, 3, 21, 4, 16, 17, 15, 9, 7, 10, 3, 1, 2, 1, 5, 6, 3, 2, 1, 3, 2, 7, 9, 2, 2, 2, 1, 2, 2, 4, 2, 14, 7, 2, 1, 1, 3, 2, 3, 2, 7, 5, 7, 4, 2, 8, 2, 4, 2, 5, 9, 5, 4, 8, 2, 3, 2, 12, 2, 2, 2, 10, 2, 2, 2, 2, 2, 2, 4, 2, 3, 16, 2, 2, 6, 3, 2, 2, 2, 2, 5, 12, 3, 3, 8, 3, 4, 2, 2, 9, 6, 2, 3, 4, 2, 4, 6, 1, 5, 2, 2, 1, 1, 1, 1, 5, 2, 2, 2, 1, 1, 1, 1, 1, 1, 1, 1, 2, 1, 1, 2, 2, 1, 1, 1, 3, 4, 5, 3, 2, 1, 5, 2, 2, 6, 2, 1, 4, 1, 1, 1, 3, 2, 2, 3, 2, 2, 2, 1, 1, 1, 2, 1, 1, 1, 1, 1, 2, 3, 5, 1, 1, 2, 1, 1, 2, 1, 2, 2, 2, 1, 1, 1, 1, 3, 3, 1, 1, 1, 1, 2, 1, 2, 1, 2, 2, 2, 1, 1, 3, 2, 1, 1, 3, 3, 3, 1, 1, 2, 1, 1, 2, 1, 1, 1, 1, 1, 1, 1, 2, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 2, 2, 4, 1, 1, 2, 1, 1, 1, 1, 1, 2, 1, 1, 2, 1, 1, 1, 1, 1, 1, 1, 1, 1, 2, 2, 1, 1, 1, 1, 2, 2, 1, 1, 1, 1, 3, 1, 2, 1, 2, 2, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 2, 1, 3, 1, 2, 1, 1, 1, 1, 1, 2, 1, 1, 1, 2, 1, 1, 1, 1, 2, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 2, 2, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1

[3828, 1549, 158, 23, 209, 86, 19, 26, 19, 18, 1179, 145, 551, 42, 23, 49, 49, 110, 298, 518, 455, 68, 47, 310, 254, 29, 48, 49, 201, 75, 70, 27, 15, 118, 714, 12, 43, 123, 50, 42, 124, 730, 306, 128, 188, 78, 137, 276, 565, 786, 61, 682, 634, 60, 467, 261, 97, 115, 127, 260, 368, 112, 16, 15, 165, 20, 112, 19, 15, 348, 1493, 164, 83, 307, 396, 520, 57, 155, 197, 65, 13, 71, 93, 306, 209, 6, 26, 55, 326, 21, 39, 8, 97, 132, 23, 23, 142, 97, 52, 212, 92, 161, 191, 15, 23, 2, 242, 450, 209, 53, 95, 38, 57, 63, 21, 89, 41, 7, 63, 155, 94, 113, 12, 70, 88, 242, 33, 75, 129, 40, 1, 3, 315, 118, 39, 167, 12, 43, 227, 87, 90, 270, 16, 176, 1, 9, 29, 60, 555, 249, 241, 52, 74, 25, 86, 93, 34, 95, 9, 189, 290, 80, 25, 87, 256, 264, 233, 12, 7, 4, 42, 134, 11, 161, 17, 4, 314, 905, 23, 26, 32, 21, 207, 29, 14, 284, 61, 89, 836, 120, 186, 336, 14, 44, 4, 358, 42, 144, 254, 21, 409, 63, 39, 52, 168, 25, 149, 247, 170, 36, 16, 42, 114, 59, 85, 80, 273, 138, 313, 49, 65, 10, 29, 47, 8, 1, 7, 13, 46,

[5, 15, 11, 11, 67, 192, 274, 12, 42, 1, 2, 41, 2, 3, 8, 18, 7, 6, 77, 1, 9, 5, 1, 1, 18, 31, 15, 2, 2, 2, 10, 57, 7, 42, 1, 70, 1, 2, 10, 33, 2, 5, 1, 1, 36, 10, 82, 19, 1, 15, 9, 1, 44, 118, 33, 5, 6, 1, 2, 1, 9, 51, 3, 2, 1, 2, 28, 11, 2, 2, 2, 1, 27, 23, 1, 1, 17, 2, 1, 2, 1, 13, 1, 1, 14, 17, 38, 3, 1, 57, 1, 1, 1, 11, 7, 46, 7, 1, 1, 19, 4, 4, 35, 4, 5, 60, 2, 12, 10, 5, 51, 198, 4, 150, 12, 13, 81, 43, 8, 1, 290, 10, 29, 19, 1, 7, 2, 4, 10, 12, 25, 1, 6, 6, 13, 3, 10, 1, 6, 33, 8, 13, 11, 6, 5, 1, 2, 2, 1, 6, 2, 1, 2, 3, 1, 4, 31, 2, 1, 17, 2, 1, 1, 5, 5, 5, 1, 9, 10, 26, 1, 3, 1, 59, 4, 3, 1, 2, 3, 5, 8, 11, 1, 1, 8, 1, 5, 1, 6, 57, 1, 1, 3, 45, 7, 17, 22, 48, 51, 74, 14, 8, 8, 8, 7, 53, 41, 117, 5, 14, 4, 5, 2, 53, 4, 12, 6, 2, 19, 4, 2, 4, 6, 2, 42, 2, 6, 8, 6, 2, 2, 6, 14, 9, 3, 10, 43, 12, 2, 25, 4, 4, 4, 50, 11, 63, 28, 17, 2, 13, 12, 3, 2, 17, 6, 12, 14, 45, 17, 41, 105, 6, 46, 31, 8, 13, 8, 8, 12, 38, 21, 36, 6, 4, 13, 38, 4, 5, 13, 20, 13, 25, 4, 6, 31, 32, 3, 13, 11, 1

[10, 6, 1, 1, 5, 3, 1, 14, 12, 1, 1, 1, 2, 6, 7, 21, 5, 4, 9, 7, 1, 9, 5, 2, 1, 1, 1, 2, 2, 5, 7, 2, 3, 4, 1, 1, 6, 1, 1, 1, 18, 1, 1, 3, 1, 7, 2, 4, 2, 2, 4, 1, 3, 1, 1, 2, 11, 2, 1, 1, 3, 2, 6, 1, 3, 3, 1, 5, 2, 1, 2, 3, 1, 2, 2, 4, 2, 1, 2, 1, 1, 2, 3, 2, 1, 3, 1, 1, 2, 1, 2, 2, 1, 1, 1, 5, 2, 1, 1, 1, 1, 2, 1, 1, 1, 1, 1, 1, 1, 2, 1, 1, 1, 1, 1, 1, 1, 4, 2, 1, 2, 5, 1, 1, 1, 1, 1, 2, 2, 1, 1, 2, 2, 4, 3, 3, 3, 2, 1, 8, 7, 1, 2, 1, 3, 6, 5, 2, 2, 1, 1, 1, 2, 2, 7, 1, 2, 5, 1, 1, 1, 1, 2, 6, 3, 3, 3, 3, 1, 1, 1, 2, 4, 2, 1, 1, 1, 2, 1, 1, 2, 1, 1, 1, 1, 2, 5, 1, 3, 3, 2, 1, 1, 2, 1, 1, 1, 2, 1, 1, 2, 2, 1, 3, 2, 3, 1, 2, 1, 1, 2, 1, 4, 2, 1, 1, 1, 5, 3, 1, 1, 1, 1, 1, 1, 3, 1, 1, 10, 1, 2, 2, 6, 2, 2, 1, 4, 1, 1, 1, 1, 1, 1, 5, 1, 2, 1, 2, 1, 1, 1, 1, 1, 3, 1, 1, 2, 2, 1, 4, 2, 5, 1, 1, 4, 1, 2, 2, 1, 1, 1, 2, 2, 1, 1, 1, 2, 1, 1, 1, 1, 1, 1, 2, 1, 1, 1, 1, 1, 1, 1, 1, 1, 2, 1, 3, 1, 1, 1, 5, 1, 1, 1, 2, 1, 2, 3, 1, 2, 1, 2, 2, 1, 1, 1, 2, 1, 3, 1, 1, 1, 1, 1, 1, 1, 2, 4, 1, 1, 2, 2,

...

[252, 69, 36, 29, 30, 24, 7, 1, 10, 16, 112, 15, 15, 21, 3, 11, 1, 21, 8, 74, 9, 14, 10, 11, 2, 2, 9, 290, 21, 3, 15, 7, 49, 15, 3, 7, 24, 10, 9, 1, 7, 12, 7, 52, 1, 45, 14, 66, 96, 106, 7, 19, 2, 27, 230, 1, 10, 22, 2, 7, 2, 5, 13, 17, 47, 1, 1, 5, 24, 9, 12, 1, 11, 1, 5, 1, 52, 70, 2, 3, 44, 5, 11, 1, 26, 11, 1, 44, 1, 9, 20, 6, 2, 28, 11, 13, 2, 4, 10, 4, 32, 20, 114, 27, 9, 27, 5, 142, 18, 28, 4, 2, 3, 2, 47, 7, 1, 5, 35, 15, 13, 31, 2, 3, 1, 249, 1, 5, 8, 3, 19, 5, 2, 7, 5, 1, 79, 38, 4, 1, 1, 5, 19, 1, 3, 1, 1, 1, 8, 10, 4, 43, 108, 65, 6, 3, 13, 1, 6, 75, 3, 32, 5, 83, 1, 12, 15, 44, 4, 15, 11, 43, 16, 10, 17, 14, 50, 1, 133, 24, 6, 36, 27, 54, 7, 23, 47, 4, 19, 14, 4, 21, 12, 1, 10, 22, 99, 21, 65, 8, 44, 3, 1, 89, 15, 10, 17, 6, 36, 3, 12, 21, 4, 8, 46, 64, 5, 15, 9, 2, 20, 1, 13, 8, 25, 3, 12, 8, 29, 1, 7, 61, 126, 16, 1, 6, 1, 8, 13, 12, 3, 1, 18, 2, 11, 10, 31, 92, 83, 22, 54, 7, 1, 28, 3, 5, 1, 3, 1, 3, 1, 17, 3, 21, 5, 5, 3, 4, 4, 15, 14, 8, 104, 9, 4, 11, 2, 2, 29, 10, 1

[1, 56, 26, 25, 1, 1, 1, 1, 1, 1, 11, 16, 3, 3, 9, 3, 4, 1, 3, 8, 2, 8, 1, 1, 9, 8, 2, 5, 7, 1, 7, 3, 16, 1, 3, 1, 2, 4, 1, 1, 8, 6, 18, 2, 2, 6, 1, 2, 6, 13, 2, 2, 6, 1, 1, 1, 1, 2, 1, 3, 1, 2, 2, 2, 3, 1, 1, 1, 2, 4, 1, 1, 1, 1, 1, 1, 4, 1, 1, 1, 1, 1, 1, 1, 2, 2, 5, 5, 7, 3, 1, 1, 1, 1, 2, 2, 6, 14, 7, 2, 4, 7, 9, 8, 3, 9, 3, 15, 5, 3, 2, 2, 2, 2, 2, 3, 3, 2, 1, 7, 1, 2, 1, 5, 1, 1, 6, 1, 4, 1, 1, 1, 1, 1, 1, 1, 4, 4, 1, 1, 2, 1, 1, 4, 7, 1, 1, 1, 1, 3, 4, 4, 1, 3, 7, 2, 1, 2, 2, 2, 2, 1, 1, 2, 1, 2, 1, 2, 5, 2, 2, 1, 1, 1, 2, 1, 1, 1, 1, 1, 1, 1, 2, 1, 2, 1, 1, 1, 1, 1, 2, 2, 1, 1, 1, 1, 2, 1, 3, 1, 1, 1, 1, 2, 2, 4, 3, 2, 1, 1, 3, 3, 1, 1, 1, 1, 1, 2, 2, 2, 1, 1, 1, 2, 1, 2, 8, 2, 1, 8, 1, 1, 2, 2, 1, 4, 3, 1, 1, 1, 1, 1, 1, 2, 2, 2, 6, 8, 1, 1, 1, 2, 1, 1, 1, 1, 1, 2, 2, 1, 1, 3, 2, 2, 4, 7, 3, 1, 1, 1, 1, 4, 2, 2, 4, 1, 1, 1, 1, 4, 1, 2, 4, 1, 1, 1, 1, 1, 1, 3, 1, 2, 1, 1, 1, 1, 1, 1, 1, 2, 1, 4, 1, 3, 6, 2, 1, 1, 1, 1, 2, 3, 2, 1, 2, 1, 1, 1, 1, 2, 1, 2, 1, 1, 1, 1, 1, 1, 1, 1,

[1, 4, 1, 1, 1, 1, 1, 5, 2, 2, 2, 2, 3, 2, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 2, 1, 1, 2, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 2, 2, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1]
[1, 1, 1, 1, 1, 1, 1, 2, 3, 2, 2, 2, 4, 3, 3, 1, 2, 1, 1, 1, 1, 1, 1, 1, 2, 3, 1, 4, 4, 5, 3, 2, 2, 1, 2, 1, 2, 1, 1, 2, 1, 1, 1, 1, 2, 1, 2, 1, 1, 1, 1, 1, 2, 1, 1, 1, 1, 1, 1, 1, 1, 2, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1]
[1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 4, 3, 4, 6, 4, 2, 1, 1, 1, 1, 1, 1, 1, 1, 3, 1, 1, 1, 1, 1, 1, 3, 1, 1, 3, 1, 1, 1, 1, 1, 1, 2, 1, 1, 1, 1, 1, 1, 1, 1, 3, 1, 2, 1, 2, 2, 2, 2, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 2, 1, 1, 1, 1, 2, 1, 1, 1, 1, 1, 1, 1, 1]
[1, 1, 1, 1, 1, 1, 1, 6, 6, 4, 4, 3, 2, 2, 1, 1, 1, 1, 2, 1, 1, 3, 2, 2, 1, 1, 1, 2, 2, 1, 1, 1, 1, 1, 3, 1, 1, 1, 1, 2, 1, 1, 1, 1, 1, 1, 2, 1, 1, 2, 1, 1, 1, 1, 2, 1, 1, 1, 1, 1, 1, 1, 1, 1, 2, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1]
[1, 1, 1, 1, 1, 1, 4, 1, 1, 3, 1, 1, 1, 1,

[2, 2, 3, 11, 12, 29, 15, 9, 56, 1, 1, 15, 188, 1, 1, 40, 10, 1, 4, 41, 22, 149, 150, 422, 410, 1, 2, 49, 156, 7, 1, 5, 5, 67, 35, 27, 5, 27, 53, 82, 116, 69, 140, 307, 270, 472, 473, 7, 3, 32, 76, 9, 44, 202, 2, 4, 2, 7, 16, 2, 30, 9, 11, 24, 4, 53, 17, 11, 15, 24, 16, 142, 6, 1, 10, 103, 74, 1, 1, 2, 6, 4, 4, 2, 14, 1, 9, 1, 1, 20, 97, 2, 2, 47, 7, 38, 3, 42, 2, 27, 34, 56, 1, 21, 66, 93, 86, 16, 11, 37, 1, 7, 4, 25, 3, 12, 15, 1, 18, 3, 12, 1, 1, 20, 7, 12, 5, 16, 1, 5, 9, 1, 1, 8, 13, 39, 2, 27, 6, 4, 7, 17, 6, 1, 38, 4, 188, 4, 11, 1, 134, 103, 6, 2, 3, 1, 1, 6, 35, 7, 3, 1, 16, 3, 1, 1, 21, 1, 1, 1, 1, 1, 4, 1, 1, 9, 1, 9, 1, 1, 9, 5, 3, 1, 10, 107, 9, 1, 1, 9, 9, 51, 50, 38, 36, 36, 33, 33, 1, 60, 9, 1, 9, 1, 10, 1, 33, 69, 74, 30, 51, 23, 1, 31, 11, 17, 9, 2, 2, 4, 55, 3, 2, 3, 3, 6, 38, 3, 18, 34, 4, 3, 3, 18, 26, 21, 39, 20, 26, 22, 2, 1, 3, 6, 4, 1, 2, 36, 4, 4, 14, 6, 83, 38, 24, 1, 52, 1, 1, 2, 4, 4, 1, 2, 5, 10, 16, 21, 8, 4, 34, 34, 4, 47, 4, 1, 22, 20, 55, 3, 3, 4, 3, 1

KeyboardInterrupt: 

In [130]:
labeled_set = pd.DataFrame(M, columns=dictionary)

In [131]:
labeled_set.head()

wetransf  f0qu8  ngundik   யங  rheumatologist  unthread  cwfn  \
0  0.005747       0.0    0.0      0.0  0.0             0.0       0.0   0.0   
1  0.005155       0.0    0.0      0.0  0.0             0.0       0.0   0.0   
2  0.005650       0.0    0.0      0.0  0.0             0.0       0.0   0.0   
3  0.007042       0.0    0.0      0.0  0.0             0.0       0.0   0.0   
4  0.000034       0.0    0.0      0.0  0.0             0.0       0.0   0.0   

   silvio  criminalis  ...   keno  quillaia  constantli  corinthia  \
0     0.0         0.0  ...    0.0       0.0    0.000000        0.0   
1     0.0         0.0  ...    0.0       0.0    0.000000        0.0   
2     0.0         0.0  ...    0.0       0.0    0.000000        0.0   
3     0.0         0.0  ...    0.0       0.0    0.000000        0.0   
4     0.0         0.0  ...    0.0       0.0    0.000034        0.0   

   fasciolopsiasi  makinghomeafford  brinjal  rueda  jcmc  bari  
0             0.0               0.0      0.0    0.0   0.0   0.0  
1             0.0               0.0      0.0    0.0   0.0   0.0  
2             0.0               0.0      0.0    0.0   0.0   0.0  
3             0.0               0.0      0.0    0.0   0.0   0.0  
4             0.0               0.0      0.0    0.0   0.0   0.0  

[5 rows x 117244 columns]

In [147]:
digit_stems = []
for col in labeled_set.columns:
    if col.isdigit():
        digit_stems.append(col)        

In [148]:
len(digit_stems)

10110

In [149]:
labeled_set['digits'] = labeled_set[digit_stems].apply(sum,axis=1)

In [151]:
labeled_set.hea

wetransf  f0qu8  ngundik   யங  rheumatologist  unthread  cwfn  \
0  0.005747       0.0    0.0      0.0  0.0             0.0       0.0   0.0   
1  0.005155       0.0    0.0      0.0  0.0             0.0       0.0   0.0   
2  0.005650       0.0    0.0      0.0  0.0             0.0       0.0   0.0   
3  0.007042       0.0    0.0      0.0  0.0             0.0       0.0   0.0   
4  0.000034       0.0    0.0      0.0  0.0             0.0       0.0   0.0   

   silvio  criminalis    ...     quillaia  constantli  corinthia  \
0     0.0         0.0    ...          0.0    0.000000        0.0   
1     0.0         0.0    ...          0.0    0.000000        0.0   
2     0.0         0.0    ...          0.0    0.000000        0.0   
3     0.0         0.0    ...          0.0    0.000000        0.0   
4     0.0         0.0    ...          0.0    0.000034        0.0   

   fasciolopsiasi  makinghomeafford  brinjal  rueda  jcmc  bari    digits  
0             0.0               0.0      0.0    0.0   0.0   0.0  0.000000  
1             0.0               0.0      0.0    0.0   0.0   0.0  0.000000  
2             0.0               0.0      0.0    0.0   0.0   0.0  0.000000  
3             0.0               0.0      0.0    0.0   0.0   0.0  0.070423  
4             0.0               0.0      0.0    0.0   0.0   0.0  0.020084  

[5 rows x 117245 columns]

In [152]:
labeled_set = labeled_set.drop(digit_stems, axis=1)

In [153]:
len(labeled_set.columns)

107135

In [154]:
labeled_set.to_pickle('data/labeled_set_type.pkl')